In [16]:
import os # Operating System
import numpy as np
import pandas as pd
import datetime as dt # Datetime
import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

!conda install -c conda-forge folium=0.5.0 --yes
import folium #import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


In [17]:
#Read the data for examination (Source: http://landregistry.data.gov.uk/)
df_ppd = pd.read_csv("http://prod2.publicdata.landregistry.gov.uk.s3-website-eu-west-1.amazonaws.com/pp-2018.csv")

In [18]:
df_ppd.head(5)

{666758D7-43A9-3363-E053-6B04A8C0D74E}  405000  2018-01-25 00:00  WR15 8LH  \
0  {666758D7-43AA-3363-E053-6B04A8C0D74E}  315000  2018-01-23 00:00   SY7 8QA   
1  {666758D7-43AD-3363-E053-6B04A8C0D74E}  165000  2018-01-19 00:00   SY1 2BF   
2  {666758D7-43B0-3363-E053-6B04A8C0D74E}  370000  2018-01-22 00:00   SY8 4DF   
3  {666758D7-43B3-3363-E053-6B04A8C0D74E}  320000  2018-01-19 00:00  TF10 7ET   
4  {666758D7-43B4-3363-E053-6B04A8C0D74E}  180000  2018-01-31 00:00   SY3 0NQ   

   D  N  F RAMBLERS WAY Unnamed: 8        Unnamed: 9          BORASTON  \
0  D  N  F  MONT CENISE        NaN               NaN              CLUN   
1  T  Y  F           42        NaN        PENSON WAY               NaN   
2  D  N  F   WILLOW HEY        NaN               NaN  ASHFORD CARBONEL   
3  D  N  F            3        NaN  PRINCESS GARDENS               NaN   
4  S  N  F           79        NaN     LYTHWOOD ROAD      BAYSTON HILL   

  TENBURY WELLS  SHROPSHIRE SHROPSHIRE.1  A A.1  
0   CRAVEN ARMS  SHROPSHIRE   SHROPSHIRE  A   A  
1    SHREWSBURY  SHROPSHIRE   SHROPSHIRE  A   A  
2        LUDLOW  SHROPSHIRE   SHROPSHIRE  A   A  
3       NEWPORT      WREKIN       WREKIN  A   A  
4    SHREWSBURY  SHROPSHIRE   SHROPSHIRE  A   A

In [19]:
df_ppd.shape


(1029799, 16)

In [20]:
# Assign meaningful column names
df_ppd.columns = ['TUID', 'Price', 'Date_Transfer', 'Postcode', 'Prop_Type', 'Old_New', 'Duration', 'PAON', \
                  'SAON', 'Street', 'Locality', 'Town_City', 'District', 'County', 'PPD_Cat_Type', 'Record_Status']

In [21]:
# Format the date column
df_ppd['Date_Transfer'] = df_ppd['Date_Transfer'].apply(pd.to_datetime)

# Delete all obsolete transactions which were done before 2016
df_ppd.drop(df_ppd[df_ppd.Date_Transfer.dt.year < 2016].index, inplace=True)

# Sort by Date of Sale
df_ppd.sort_values(by=['Date_Transfer'],ascending=[False],inplace=True)

In [22]:
df_ppd_london = df_ppd.query("Town_City == 'LONDON'")

# Make a list of street names in LONDON
streets = df_ppd_london['Street'].unique().tolist()

In [23]:
df_grp_price = df_ppd_london.groupby(['Street'])['Price'].mean().reset_index()

# Give meaningful names to the columns
df_grp_price.columns = ['Street', 'Avg_Price']

In [24]:
#Input your Budget's Upper Limit and Lower Limit - Find the locations df_grp_price which fits your budget
df_affordable = df_grp_price.query("(Avg_Price >= 2200000) & (Avg_Price <= 2500000)")

In [25]:
# Display the dataframe
df_affordable

Street     Avg_Price
196                ALBION SQUARE  2.450000e+06
390                  ANHALT ROAD  2.435000e+06
405              ANSDELL TERRACE  2.250000e+06
422              APPLEGARTH ROAD  2.400000e+06
855              BARONSMEAD ROAD  2.375000e+06
981               BEAUCLERC ROAD  2.480000e+06
1102             BELVEDERE DRIVE  2.340000e+06
1215           BICKENHALL STREET  2.208500e+06
1253           BIRCHLANDS AVENUE  2.217000e+06
1553              BRAMPTON GROVE  2.456875e+06
1632           BRIARDALE GARDENS  2.397132e+06
1797                    BROOKWAY  2.400000e+06
1914                BURBAGE ROAD  2.445000e+06
1980                   BURY WALK  2.492500e+06
2068             CALLCOTT STREET  2.375000e+06
2129           CAMPDEN HILL ROAD  2.379653e+06
2136                CAMPION ROAD  2.461000e+06
2158               CANNING PLACE  2.425000e+06
2225               CARLISLE ROAD  2.200000e+06
2230             CARLTON GARDENS  2.483500e+06
2242               CARLYLE COURT  2.300000e+06
2406              CHALCOT SQUARE  2.286679e+06
2484                CHARLES LANE  2.414000e+06
2562            CHELSEA CRESCENT  2.495000e+06
2606         CHESTER CLOSE NORTH  2.450000e+06
2638                CHEYNE COURT  2.250000e+06
2641                  CHEYNE ROW  2.410000e+06
2686               CHISWICK MALL  2.287500e+06
2761                   CITY ROAD  2.468340e+06
2808            CLARENDON STREET  2.250000e+06
2900            CLONCURRY STREET  2.388333e+06
2944                COLBECK MEWS  2.367500e+06
2995            COLLEGE CRESCENT  2.440000e+06
3202       CORNWALL TERRACE MEWS  2.350000e+06
3255          COURT LANE GARDENS  2.360000e+06
3377              CRESCENT GROVE  2.298000e+06
3583               DALEBURY ROAD  2.400000e+06
3848               DEWHURST ROAD  2.425000e+06
3929                  DORIA ROAD  2.362500e+06
3980              DOWNSHIRE HILL  2.225000e+06
4035                DUCHESS WALK  2.477500e+06
4232       ECCLESTON SQUARE MEWS  2.335500e+06
4285               EGBERT STREET  2.265000e+06
4289               EGERTON PLACE  2.200000e+06
4375               ELM PARK ROAD  2.320425e+06
4894               FLORAL STREET  2.227222e+06
5016             FRANK DIXON WAY  2.212500e+06
5098                 FULTON MEWS  2.299000e+06
5241                 GERARD ROAD  2.258500e+06
5244                GERRARD ROAD  2.242500e+06
5289               GIRDLERS ROAD  2.441667e+06
5382         GLOUCESTER CRESCENT  2.350833e+06
5450                GORDON PLACE  2.477000e+06
5486              GRAFTON SQUARE  2.270000e+06
5493              GRAHAM TERRACE  2.325000e+06
5952                HARMAN DRIVE  2.262500e+06
5976               HARRIS STREET  2.471769e+06
6039             HAVANNAH STREET  2.217309e+06
6111              HAZLEWELL ROAD  2.500000e+06
6227               HEREFORD MEWS  2.310000e+06
6247            HERONDALE AVENUE  2.475000e+06
6344        HIGHGATE HIGH STREET  2.211000e+06
6359               HIGHWOOD HILL  2.252500e+06
6395              HILLGATE PLACE  2.200000e+06
6506           HOLLYCROFT AVENUE  2.361375e+06
6510              HOLLYWOOD MEWS  2.350000e+06
6555              HONEYWELL ROAD  2.278333e+06
6611              HORTENSIA ROAD  2.275917e+06
6640               HOXTON SQUARE  2.234286e+06
6666                 HUNTER ROAD  2.300000e+06
6825               JACKSONS LANE  2.362500e+06
6885                 JOHN STREET  2.235000e+06
7190            KINNERTON STREET  2.485600e+06
7224         KNARESBOROUGH PLACE  2.325000e+06
7244                 KNOX STREET  2.250000e+06
7264              LADBROKE GROVE  2.483300e+06
7333              LANCASTER MEWS  2.312500e+06
7403              LANSDOWNE ROAD  2.364876e+06
7432   LATIMER INDUSTRIAL ESTATE  2.400000e+06
7485                LAXTON PLACE  2.500000e+06
7687              LINCOLN AVENUE  2.203500e+06
7716              LINGFIELD ROAD  2.248750e+06
7745               LISSON STREET  2.462500e+06
7779             LIVERPOOL GROVE  2.288000e+06
7871              LONGWOOD DRIV

In [26]:
import pandas as pd
import numpy as np
import datetime as DT
import hmac
from geopy.geocoders import Nominatim
from geopy.distance import vincenty
# import k-means from clustering stage
from sklearn.cluster import KMeans

In [27]:
for index, item in df_affordable.iterrows():
    print(f"index: {index}")
    print(f"item: {item}")
    print(f"item.Street only: {item.Street}")

index: 196
item: Street       ALBION SQUARE
Avg_Price         2.45e+06
Name: 196, dtype: object
item.Street only: ALBION SQUARE
index: 390
item: Street       ANHALT ROAD
Avg_Price      2.435e+06
Name: 390, dtype: object
item.Street only: ANHALT ROAD
index: 405
item: Street       ANSDELL TERRACE
Avg_Price           2.25e+06
Name: 405, dtype: object
item.Street only: ANSDELL TERRACE
index: 422
item: Street       APPLEGARTH ROAD
Avg_Price            2.4e+06
Name: 422, dtype: object
item.Street only: APPLEGARTH ROAD
index: 855
item: Street       BARONSMEAD ROAD
Avg_Price          2.375e+06
Name: 855, dtype: object
item.Street only: BARONSMEAD ROAD
index: 981
item: Street       BEAUCLERC ROAD
Avg_Price          2.48e+06
Name: 981, dtype: object
item.Street only: BEAUCLERC ROAD
index: 1102
item: Street       BELVEDERE DRIVE
Avg_Price           2.34e+06
Name: 1102, dtype: object
item.Street only: BELVEDERE DRIVE
index: 1215
item: Street       BICKENHALL STREET
Avg_Price           2.2085e+06
N

In [28]:
geolocator = Nominatim()


/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Using Nominatim with the default "geopy/1.22.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  """Entry point for launching an IPython kernel.


In [29]:
df_affordable['city_coord'] = df_affordable['Street'].apply(geolocator.geocode).apply(lambda x: (x.latitude, x.longitude))

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [30]:
df_affordable

Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
390                  ANHALT ROAD  2.435000e+06   
405              ANSDELL TERRACE  2.250000e+06   
422              APPLEGARTH ROAD  2.400000e+06   
855              BARONSMEAD ROAD  2.375000e+06   
981               BEAUCLERC ROAD  2.480000e+06   
1102             BELVEDERE DRIVE  2.340000e+06   
1215           BICKENHALL STREET  2.208500e+06   
1253           BIRCHLANDS AVENUE  2.217000e+06   
1553              BRAMPTON GROVE  2.456875e+06   
1632           BRIARDALE GARDENS  2.397132e+06   
1797                    BROOKWAY  2.400000e+06   
1914                BURBAGE ROAD  2.445000e+06   
1980                   BURY WALK  2.492500e+06   
2068             CALLCOTT STREET  2.375000e+06   
2129           CAMPDEN HILL ROAD  2.379653e+06   
2136                CAMPION ROAD  2.461000e+06   
2158               CANNING PLACE  2.425000e+06   
2225               CARLISLE ROAD  2.200000e+06   
2230             CARLTON GARDENS  2.483500e+06   
2242               CARLYLE COURT  2.300000e+06   
2406              CHALCOT SQUARE  2.286679e+06   
2484                CHARLES LANE  2.414000e+06   
2562            CHELSEA CRESCENT  2.495000e+06   
2606         CHESTER CLOSE NORTH  2.450000e+06   
2638                CHEYNE COURT  2.250000e+06   
2641                  CHEYNE ROW  2.410000e+06   
2686               CHISWICK MALL  2.287500e+06   
2761                   CITY ROAD  2.468340e+06   
2808            CLARENDON STREET  2.250000e+06   
2900            CLONCURRY STREET  2.388333e+06   
2944                COLBECK MEWS  2.367500e+06   
2995            COLLEGE CRESCENT  2.440000e+06   
3202       CORNWALL TERRACE MEWS  2.350000e+06   
3255          COURT LANE GARDENS  2.360000e+06   
3377              CRESCENT GROVE  2.298000e+06   
3583               DALEBURY ROAD  2.400000e+06   
3848               DEWHURST ROAD  2.425000e+06   
3929                  DORIA ROAD  2.362500e+06   
3980              DOWNSHIRE HILL  2.225000e+06   
4035                DUCHESS WALK  2.477500e+06   
4232       ECCLESTON SQUARE MEWS  2.335500e+06   
4285               EGBERT STREET  2.265000e+06   
4289               EGERTON PLACE  2.200000e+06   
4375               ELM PARK ROAD  2.320425e+06   
4894               FLORAL STREET  2.227222e+06   
5016             FRANK DIXON WAY  2.212500e+06   
5098                 FULTON MEWS  2.299000e+06   
5241                 GERARD ROAD  2.258500e+06   
5244                GERRARD ROAD  2.242500e+06   
5289               GIRDLERS ROAD  2.441667e+06   
5382         GLOUCESTER CRESCENT  2.350833e+06   
5450                GORDON PLACE  2.477000e+06   
5486              GRAFTON SQUARE  2.270000e+06   
5493              GRAHAM TERRACE  2.325000e+06   
5952                HARMAN DRIVE  2.262500e+06   
5976               HARRIS STREET  2.471769e+06   
6039             HAVANNAH STREET  2.217309e+06   
6111              HAZLEWELL ROAD  2.500000e+06   
6227               HEREFORD MEWS  2.310000e+06   
6247            HERONDALE AVENUE  2.475000e+06   
6344        HIGHGATE HIGH STREET  2.211000e+06   
6359               HIGHWOOD HILL  2.252500e+06   
6395              HILLGATE PLACE  2.200000e+06   
6506           HOLLYCROFT AVENUE  2.361375e+06   
6510              HOLLYWOOD MEWS  2.350000e+06   
6555              HONEYWELL ROAD  2.278333e+06   
6611              HORTENSIA ROAD  2.275917e+06   
6640               HOXTON SQUARE  2.234286e+06   
6666                 HUNTER ROAD  2.300000e+06   
6825               JACKSONS LANE  2.362500e+06   
6885                 JOHN STREET  2.235000e+06   
7190            KINNERTON STREET  2.485600e+06   
7224         KNARESBOROUGH PLACE  2.325000e+06   
7244                 KNOX STREET  2.250000e+06   
7264              LADBROKE GROVE  2.483300e+06   
7333              LANCASTER MEWS  2.312500e+06   
7403              LANSDOWNE ROAD  2.364876e+06   
7432   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7485                LAXTON

In [31]:
df_affordable[['Latitude', 'Longitude']] = df_affordable['city_coord'].apply(pd.Series)


/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/pandas/core/frame.py:2963: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [32]:
df_affordable


Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
390                  ANHALT ROAD  2.435000e+06   
405              ANSDELL TERRACE  2.250000e+06   
422              APPLEGARTH ROAD  2.400000e+06   
855              BARONSMEAD ROAD  2.375000e+06   
981               BEAUCLERC ROAD  2.480000e+06   
1102             BELVEDERE DRIVE  2.340000e+06   
1215           BICKENHALL STREET  2.208500e+06   
1253           BIRCHLANDS AVENUE  2.217000e+06   
1553              BRAMPTON GROVE  2.456875e+06   
1632           BRIARDALE GARDENS  2.397132e+06   
1797                    BROOKWAY  2.400000e+06   
1914                BURBAGE ROAD  2.445000e+06   
1980                   BURY WALK  2.492500e+06   
2068             CALLCOTT STREET  2.375000e+06   
2129           CAMPDEN HILL ROAD  2.379653e+06   
2136                CAMPION ROAD  2.461000e+06   
2158               CANNING PLACE  2.425000e+06   
2225               CARLISLE ROAD  2.200000e+06   
2230             CARLTON GARDENS  2.483500e+06   
2242               CARLYLE COURT  2.300000e+06   
2406              CHALCOT SQUARE  2.286679e+06   
2484                CHARLES LANE  2.414000e+06   
2562            CHELSEA CRESCENT  2.495000e+06   
2606         CHESTER CLOSE NORTH  2.450000e+06   
2638                CHEYNE COURT  2.250000e+06   
2641                  CHEYNE ROW  2.410000e+06   
2686               CHISWICK MALL  2.287500e+06   
2761                   CITY ROAD  2.468340e+06   
2808            CLARENDON STREET  2.250000e+06   
2900            CLONCURRY STREET  2.388333e+06   
2944                COLBECK MEWS  2.367500e+06   
2995            COLLEGE CRESCENT  2.440000e+06   
3202       CORNWALL TERRACE MEWS  2.350000e+06   
3255          COURT LANE GARDENS  2.360000e+06   
3377              CRESCENT GROVE  2.298000e+06   
3583               DALEBURY ROAD  2.400000e+06   
3848               DEWHURST ROAD  2.425000e+06   
3929                  DORIA ROAD  2.362500e+06   
3980              DOWNSHIRE HILL  2.225000e+06   
4035                DUCHESS WALK  2.477500e+06   
4232       ECCLESTON SQUARE MEWS  2.335500e+06   
4285               EGBERT STREET  2.265000e+06   
4289               EGERTON PLACE  2.200000e+06   
4375               ELM PARK ROAD  2.320425e+06   
4894               FLORAL STREET  2.227222e+06   
5016             FRANK DIXON WAY  2.212500e+06   
5098                 FULTON MEWS  2.299000e+06   
5241                 GERARD ROAD  2.258500e+06   
5244                GERRARD ROAD  2.242500e+06   
5289               GIRDLERS ROAD  2.441667e+06   
5382         GLOUCESTER CRESCENT  2.350833e+06   
5450                GORDON PLACE  2.477000e+06   
5486              GRAFTON SQUARE  2.270000e+06   
5493              GRAHAM TERRACE  2.325000e+06   
5952                HARMAN DRIVE  2.262500e+06   
5976               HARRIS STREET  2.471769e+06   
6039             HAVANNAH STREET  2.217309e+06   
6111              HAZLEWELL ROAD  2.500000e+06   
6227               HEREFORD MEWS  2.310000e+06   
6247            HERONDALE AVENUE  2.475000e+06   
6344        HIGHGATE HIGH STREET  2.211000e+06   
6359               HIGHWOOD HILL  2.252500e+06   
6395              HILLGATE PLACE  2.200000e+06   
6506           HOLLYCROFT AVENUE  2.361375e+06   
6510              HOLLYWOOD MEWS  2.350000e+06   
6555              HONEYWELL ROAD  2.278333e+06   
6611              HORTENSIA ROAD  2.275917e+06   
6640               HOXTON SQUARE  2.234286e+06   
6666                 HUNTER ROAD  2.300000e+06   
6825               JACKSONS LANE  2.362500e+06   
6885                 JOHN STREET  2.235000e+06   
7190            KINNERTON STREET  2.485600e+06   
7224         KNARESBOROUGH PLACE  2.325000e+06   
7244                 KNOX STREET  2.250000e+06   
7264              LADBROKE GROVE  2.483300e+06   
7333              LANCASTER MEWS  2.312500e+06   
7403              LANSDOWNE ROAD  2.364876e+06   
7432   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7485                LAXTON

In [33]:
df = df_affordable.drop(columns=['city_coord'])


In [34]:
df


Street     Avg_Price   Latitude   Longitude
196                ALBION SQUARE  2.450000e+06 -41.273758  173.289393
390                  ANHALT ROAD  2.435000e+06  51.480316   -0.166801
405              ANSDELL TERRACE  2.250000e+06  51.499890   -0.189103
422              APPLEGARTH ROAD  2.400000e+06  53.748654   -0.326670
855              BARONSMEAD ROAD  2.375000e+06  51.477315   -0.239457
981               BEAUCLERC ROAD  2.480000e+06  30.211452  -81.617981
1102             BELVEDERE DRIVE  2.340000e+06  38.072818  -78.458796
1215           BICKENHALL STREET  2.208500e+06  51.521201   -0.158908
1253           BIRCHLANDS AVENUE  2.217000e+06  51.448394   -0.160468
1553              BRAMPTON GROVE  2.456875e+06  51.589961   -0.318525
1632           BRIARDALE GARDENS  2.397132e+06  51.560175   -0.195431
1797                    BROOKWAY  2.400000e+06  45.432185 -122.802812
1914                BURBAGE ROAD  2.445000e+06  52.538507   -1.353674
1980                   BURY WALK  2.492500e+06  52.145529   -0.423593
2068             CALLCOTT STREET  2.375000e+06  51.508350   -0.198328
2129           CAMPDEN HILL ROAD  2.379653e+06  51.508111   -0.199667
2136                CAMPION ROAD  2.461000e+06  43.623321  -70.236225
2158               CANNING PLACE  2.425000e+06  51.499494   -0.185481
2225               CARLISLE ROAD  2.200000e+06  43.399438  -79.973215
2230             CARLTON GARDENS  2.483500e+06 -37.801943  144.971970
2242               CARLYLE COURT  2.300000e+06  32.972701  -97.173392
2406              CHALCOT SQUARE  2.286679e+06  51.541088   -0.155928
2484                CHARLES LANE  2.414000e+06  40.257626  -75.093891
2562            CHELSEA CRESCENT  2.495000e+06  34.522443  -85.443891
2606         CHESTER CLOSE NORTH  2.450000e+06  51.529205   -0.145081
2638                CHEYNE COURT  2.250000e+06  52.035905    0.727612
2641                  CHEYNE ROW  2.410000e+06  51.483717   -0.169603
2686               CHISWICK MALL  2.287500e+06  51.487994   -0.246605
2761                   CITY ROAD  2.468340e+06  51.529697   -0.097763
2808            CLARENDON STREET  2.250000e+06  42.284961  -71.345534
2900            CLONCURRY STREET  2.388333e+06  51.473763   -0.216244
2944                COLBECK MEWS  2.367500e+06  51.492950   -0.185921
2995            COLLEGE CRESCENT  2.440000e+06  37.282334  -76.724918
3202       CORNWALL TERRACE MEWS  2.350000e+06  51.524066   -0.157667
3255          COURT LANE GARDENS  2.360000e+06  51.448500   -0.080102
3377              CRESCENT GROVE  2.298000e+06  46.115586  -60.725330
3583               DALEBURY ROAD  2.400000e+06  51.439528   -0.163984
3848               DEWHURST ROAD  2.425000e+06  51.706072   -0.045667
3929                  DORIA ROAD  2.362500e+06  51.473116   -0.201748
3980              DOWNSHIRE HILL  2.225000e+06  51.555662   -0.170293
4035                DUCHESS WALK  2.477500e+06  51.503801   -0.076921
4232       ECCLESTON SQUARE MEWS  2.335500e+06  51.491785   -0.142260
4285               EGBERT STREET  2.265000e+06  29.782784  -95.415961
4289               EGERTON PLACE  2.200000e+06  51.364061   -0.446325
4375               ELM PARK ROAD  2.320425e+06  51.567140   -0.033635
4894               FLORAL STREET  2.227222e+06  42.698573  -71.179155
5016             FRANK DIXON WAY  2.212500e+06  51.442795   -0.080397
5098                 FULTON MEWS  2.299000e+06  51.512558   -0.184629
5241                 GERARD ROAD  2.258500e+06  51.805800    1.135193
5244                GERRARD ROAD  2.242500e+06  54.889253   -1.446589
5289               GIRDLERS ROAD  2.441667e+06  51.496697   -0.215531
5382         GLOUCESTER CRESCENT  2.350833e+06  49.631065 -118.395333
5450                GORDON PLACE  2.477000e+06  49.229958 -122.953195
5486              GRAFTON SQUARE  2.270000e+06  51.463966   -0.139084
5493              GRAHAM TERRACE  2.325000e+06  51.449574    0.114122
5952                HARMAN DRIVE  2.262500e+06  51.448159    0.096598
5976               HARRIS STREET  2.

In [35]:
address = 'London, UK'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London City are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.22.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of London City are 51.5073219, -0.1276474.


In [36]:
# create map of London using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, price, street in zip(df['Latitude'], df['Longitude'], df['Avg_Price'], df['Street']):
    label = '{}, {}'.format(street, price)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

In [37]:
#Define Foursquare Credentials and Version

CLIENT_ID = 'TM3SILTIA0FQTOSSRL2RDH5JQ4SBIURAHI0BGKGV4FWYCQ2M' # Foursquare ID
CLIENT_SECRET = 'UDGGMOMYUBWKY5G3ILU2V5ZFWN3LXBMKICEVYBEMFQY5TUAW' # Foursquare Secret
VERSION = '20181206' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: TM3SILTIA0FQTOSSRL2RDH5JQ4SBIURAHI0BGKGV4FWYCQ2M
CLIENT_SECRET:UDGGMOMYUBWKY5G3ILU2V5ZFWN3LXBMKICEVYBEMFQY5TUAW


In [38]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Street', 
                  'Street Latitude', 
                  'Street Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [43]:
# Run the above function on each location and create a new dataframe called location_venues and display it.
location_venues = getNearbyVenues(names=df['Street'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

ALBION SQUARE
ANHALT ROAD
ANSDELL TERRACE
APPLEGARTH ROAD
BARONSMEAD ROAD
BEAUCLERC ROAD
BELVEDERE DRIVE
BICKENHALL STREET
BIRCHLANDS AVENUE
BRAMPTON GROVE
BRIARDALE GARDENS
BROOKWAY
BURBAGE ROAD
BURY WALK
CALLCOTT STREET
CAMPDEN HILL ROAD
CAMPION ROAD
CANNING PLACE
CARLISLE ROAD
CARLTON GARDENS
CARLYLE COURT
CHALCOT SQUARE
CHARLES LANE
CHELSEA CRESCENT
CHESTER CLOSE NORTH
CHEYNE COURT
CHEYNE ROW
CHISWICK MALL
CITY ROAD
CLARENDON STREET
CLONCURRY STREET
COLBECK MEWS
COLLEGE CRESCENT
CORNWALL TERRACE MEWS
COURT LANE GARDENS
CRESCENT GROVE
DALEBURY ROAD
DEWHURST ROAD
DORIA ROAD
DOWNSHIRE HILL
DUCHESS WALK
ECCLESTON SQUARE MEWS
EGBERT STREET
EGERTON PLACE
ELM PARK ROAD
FLORAL STREET
FRANK DIXON WAY
FULTON MEWS
GERARD ROAD
GERRARD ROAD
GIRDLERS ROAD
GLOUCESTER CRESCENT
GORDON PLACE
GRAFTON SQUARE
GRAHAM TERRACE
HARMAN DRIVE
HARRIS STREET
HAVANNAH STREET
HAZLEWELL ROAD
HEREFORD MEWS
HERONDALE AVENUE
HIGHGATE HIGH STREET
HIGHWOOD HILL
HILLGATE PLACE
HOLLYCROFT AVENUE
HOLLYWOOD MEWS
HONEYWELL

In [44]:
location_venues

Street  Street Latitude  Street Longitude  \
0                 ALBION SQUARE       -41.273758        173.289393   
1                 ALBION SQUARE       -41.273758        173.289393   
2                 ALBION SQUARE       -41.273758        173.289393   
3                 ALBION SQUARE       -41.273758        173.289393   
4                 ALBION SQUARE       -41.273758        173.289393   
5                 ALBION SQUARE       -41.273758        173.289393   
6                 ALBION SQUARE       -41.273758        173.289393   
7                 ALBION SQUARE       -41.273758        173.289393   
8                 ALBION SQUARE       -41.273758        173.289393   
9                 ALBION SQUARE       -41.273758        173.289393   
10                ALBION SQUARE       -41.273758        173.289393   
11                ALBION SQUARE       -41.273758        173.289393   
12                ALBION SQUARE       -41.273758        173.289393   
13                ALBION SQUARE       -41.273758        173.289393   
14                ALBION SQUARE       -41.273758        173.289393   
15                ALBION SQUARE       -41.273758        173.289393   
16                ALBION SQUARE       -41.273758        173.289393   
17                ALBION SQUARE       -41.273758        173.289393   
18                ALBION SQUARE       -41.273758        173.289393   
19                ALBION SQUARE       -41.273758        173.289393   
20                ALBION SQUARE       -41.273758        173.289393   
21                ALBION SQUARE       -41.273758        173.289393   
22                ALBION SQUARE       -41.273758        173.289393   
23                ALBION SQUARE       -41.273758        173.289393   
24                ALBION SQUARE       -41.273758        173.289393   
25                ALBION SQUARE       -41.273758        173.289393   
26                ALBION SQUARE       -41.273758        173.289393   
27                  ANHALT ROAD        51.480316         -0.166801   
28                  ANHALT ROAD        51.480316         -0.166801   
29                  ANHALT ROAD        51.480316         -0.166801   
30                  ANHALT ROAD        51.480316         -0.166801   
31                  ANHALT ROAD        51.480316         -0.166801   
32                  ANHALT ROAD        51.480316         -0.166801   
33                  ANHALT ROAD        51.480316         -0.166801   
34                  ANHALT ROAD        51.480316         -0.166801   
35                  ANHALT ROAD        51.480316         -0.166801   
36                  ANHALT ROAD        51.480316         -0.166801   
37                  ANHALT ROAD        51.480316         -0.166801   
38                  ANHALT ROAD        51.480316         -0.166801   
39                  ANHALT ROAD        51.480316         -0.166801   
40                  ANHALT ROAD        51.480316         -0.166801   
41                  ANHALT ROAD        51.480316         -0.166801   
42                  ANHALT ROAD        51.480316         -0.166801   
43              ANSDELL TERRACE        51.499890         -0.189103   
44              ANSDELL TERRACE        51.499890         -0.189103   
45              ANSDELL TERRACE        51.499890         -0.189103   
46              ANSDELL TERRACE        51.499890         -0.189103   
47              ANSDELL TERRACE        51.499890         -0.189103   
48              ANSDELL TERRACE        51.499890         -0.189103   
49              ANSDELL TERRACE        51.499890         -0.189103   
50              ANSDELL TERRACE        51.499890         -0.189103   
51              ANSDELL TERRACE        51.499890         -0.189103   
52              ANSDELL TERRACE        51.499890         -0.189103   
53              ANSDELL TERRACE        51.499890         -0.189103   
54              ANSDELL TERRACE        51.499890         -0.189103   
55              ANSDELL TERRACE        51.499890         -0.189103   
56              ANSDELL TERRACE    

In [45]:
location_venues.groupby('Street').count()


Street Latitude  Street Longitude  Venue  \
Street                                                                
ALBION SQUARE                           27                27     27   
ANHALT ROAD                             16                16     16   
ANSDELL TERRACE                         46                46     46   
APPLEGARTH ROAD                          4                 4      4   
BARONSMEAD ROAD                         14                14     14   
BEAUCLERC ROAD                           4                 4      4   
BELVEDERE DRIVE                          3                 3      3   
BICKENHALL STREET                       63                63     63   
BIRCHLANDS AVENUE                        9                 9      9   
BRAMPTON GROVE                           2                 2      2   
BRIARDALE GARDENS                        5                 5      5   
BURBAGE ROAD                             5                 5      5   
BURY WALK                               15                15     15   
CALLCOTT STREET                         51                51     51   
CAMPDEN HILL ROAD                       46                46     46   
CAMPION ROAD                             3                 3      3   
CANNING PLACE                           47                47     47   
CARLTON GARDENS                         64                64     64   
CARLYLE COURT                            1                 1      1   
CHALCOT SQUARE                          53                53     53   
CHARLES LANE                             2                 2      2   
CHESTER CLOSE NORTH                     24                24     24   
CHEYNE COURT                            12                12     12   
CHEYNE ROW                              59                59     59   
CHISWICK MALL                            7                 7      7   
CITY ROAD                               28                28     28   
CLARENDON STREET                        33                33     33   
CLONCURRY STREET                        29                29     29   
COLBECK MEWS                           100               100    100   
COLLEGE CRESCENT                        16                16     16   
CORNWALL TERRACE MEWS                   47                47     47   
COURT LANE GARDENS                      12                12     12   
CRESCENT GROVE                           1                 1      1   
DALEBURY ROAD                            7                 7      7   
DEWHURST ROAD                            4                 4      4   
DORIA ROAD                              63                63     63   
DOWNSHIRE HILL                          40                40     40   
DUCHESS WALK                           100               100    100   
ECCLESTON SQUARE MEWS                  100               100    100   
EGBERT STREET                            5                 5      5   
EGERTON PLACE                            7                 7      7   
ELM PARK ROAD                           10                10     10   
FLORAL STREET                            3                 3      3   
FRANK DIXON WAY                          6                 6      6   
FULTON MEWS                             91                91     91   
GERARD ROAD                              3                 3      3   
GERRARD ROAD                             2                 2      2   
GIRDLERS ROAD                           36                36     36   
GORDON PLACE                             2                 2      2   
GRAFTON SQUARE                          85                85     85   
GRAHAM TERRACE                           2                 2      2   
HARMAN DRIVE                             4                 4      4   
HARRIS STREET                            2                 2      2   
HAVANNAH STREET                         28                28     28   
HAZLEWELL ROAD                           7         

In [46]:
# get the List of Unique Categories
print('There are {} uniques categories.'.format(len(location_venues['Venue Category'].unique())))

There are 341 uniques categories.


In [47]:
location_venues.shape


(4409, 7)

In [48]:
# one hot encoding
venues_onehot = pd.get_dummies(location_venues[['Venue Category']], prefix="", prefix_sep="")

# add street column back to dataframe
venues_onehot['Street'] = location_venues['Street'] 

# move street column to the first column
fixed_columns = [venues_onehot.columns[-1]] + list(venues_onehot.columns[:-1])

#fixed_columns
venues_onehot = venues_onehot[fixed_columns]

venues_onehot.head()

Street  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  ALBION SQUARE                  0               0                  0   
1  ALBION SQUARE                  0               0                  0   
2  ALBION SQUARE                  0               0                  0   
3  ALBION SQUARE                  0               0                  0   
4  ALBION SQUARE                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0                 0                   0                      0   
1                 0                   0                      0   
2                 0                   0                      0   
3                 0                   0                      0   
4                 0                   0                      0   

   Austrian Restaurant  Auto Garage  Automotive Shop  BBQ Joint  \
0                    0            0                0          0   
1                    0            0                0          0   
2                    0            0                0          0   
3                    0            0                0          0   
4                    0            0                0          0   

   Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Bay  Beach  \
0                0           0       0     0    1               0    0      0   
1                0           0       0     0    0               0    0      0   
2                0           0       0     0    0               0    0      0   
3                0           0       0     0    0               0    0      0   
4                0           0       0     0    0               0    0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0           0                   0   
4                0         0            0           0                   0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bistro  Boat or Ferry  \
0              0                         0          0       0              0   
1              0                         0          0       0              0   
2              0                         0          0       0              0   
3              0                         0          0       0              0   
4              0                         0          0       0              0   

   Bookstore  Botanical Garden  Boutique  Bowling Alley  Boxing Gym  \
0          0                 0         0              0           0   
1          0                 0         0              0           0   
2          0                 0         0              0           0   
3          0                 0         0              0           0   
4          0                 0         0              0           0   

   Brazilian Restaurant  Breakfast Spot  Brewer

In [49]:
london_grouped = venues_onehot.groupby('Street').mean().reset_index()
london_grouped

Street  Accessories Store  Adult Boutique  \
0                ALBION SQUARE           0.000000            0.00   
1                  ANHALT ROAD           0.000000            0.00   
2              ANSDELL TERRACE           0.000000            0.00   
3              APPLEGARTH ROAD           0.000000            0.00   
4              BARONSMEAD ROAD           0.000000            0.00   
5               BEAUCLERC ROAD           0.000000            0.00   
6              BELVEDERE DRIVE           0.000000            0.00   
7            BICKENHALL STREET           0.000000            0.00   
8            BIRCHLANDS AVENUE           0.000000            0.00   
9               BRAMPTON GROVE           0.000000            0.00   
10           BRIARDALE GARDENS           0.000000            0.00   
11                BURBAGE ROAD           0.000000            0.00   
12                   BURY WALK           0.000000            0.00   
13             CALLCOTT STREET           0.000000            0.00   
14           CAMPDEN HILL ROAD           0.000000            0.00   
15                CAMPION ROAD           0.000000            0.00   
16               CANNING PLACE           0.000000            0.00   
17             CARLTON GARDENS           0.000000            0.00   
18               CARLYLE COURT           0.000000            0.00   
19              CHALCOT SQUARE           0.000000            0.00   
20                CHARLES LANE           0.000000            0.00   
21         CHESTER CLOSE NORTH           0.000000            0.00   
22                CHEYNE COURT           0.000000            0.00   
23                  CHEYNE ROW           0.016949            0.00   
24               CHISWICK MALL           0.000000            0.00   
25                   CITY ROAD           0.000000            0.00   
26            CLARENDON STREET           0.000000            0.00   
27            CLONCURRY STREET           0.000000            0.00   
28                COLBECK MEWS           0.000000            0.00   
29            COLLEGE CRESCENT           0.000000            0.00   
30       CORNWALL TERRACE MEWS           0.000000            0.00   
31          COURT LANE GARDENS           0.000000            0.00   
32              CRESCENT GROVE           0.000000            0.00   
33               DALEBURY ROAD           0.000000            0.00   
34               DEWHURST ROAD           0.000000            0.00   
35                  DORIA ROAD           0.000000            0.00   
36              DOWNSHIRE HILL           0.000000            0.00   
37                DUCHESS WALK           0.000000            0.00   
38       ECCLESTON SQUARE MEWS           0.000000            0.00   
39               EGBERT STREET           0.000000            0.00   
40               EGERTON PLACE           0.000000            0.00   
41               ELM PARK ROAD           0.000000            0.00   
42               FLORAL STREET           0.000000            0.00   
43             FRANK DIXON WAY           0.000000            0.00   
44                 FULTON MEWS           0.000000            0.00   
45                 GERARD ROAD           0.000000            0.00   
46                GERRARD ROAD           0.000000            0.00   
47               GIRDLERS ROAD           0.000000            0.00   
48                GORDON PLACE           0.000000            0.00   
49              GRAFTON SQUARE           0.000000            0.00   
50              GRAHAM TERRACE           0.000000            0.00   
51                HARMAN DRIVE           0.000000            0.00   
52               HARRIS STREET           0.000000            0.00   
53             HAVANNAH STREET           0.000000            0.00   
54              HAZLEWELL ROAD           0.000000            0.00   
55               HEREFORD MEWS           0.000000            0.00   
56            HERONDALE AVENUE           0.000000            0.00   
57        HIGHGATE HIG

In [50]:
london_grouped.shape


(150, 342)

In [51]:
# What are the top 5 venues/facilities nearby profitable real estate investments?#

num_top_venues = 5

for hood in london_grouped['Street']:
    print("----"+hood+"----")
    temp = london_grouped[london_grouped['Street'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ALBION SQUARE----
               venue  freq
0               Café  0.22
1                Bar  0.07
2                Pub  0.07
3  Indian Restaurant  0.07
4         Restaurant  0.07


----ANHALT ROAD----
               venue  freq
0                Pub  0.25
1  French Restaurant  0.12
2      Grocery Store  0.12
3              Diner  0.06
4             Garden  0.06


----ANSDELL TERRACE----
            venue  freq
0      Restaurant  0.09
1  Clothing Store  0.09
2           Hotel  0.07
3             Pub  0.07
4       Juice Bar  0.07


----APPLEGARTH ROAD----
                   venue  freq
0                    Bar  0.25
1              Nightclub  0.25
2         Sandwich Place  0.25
3                 Casino  0.25
4  Outdoors & Recreation  0.00


----BARONSMEAD ROAD----
               venue  freq
0     Farmers Market  0.07
1        Pizza Place  0.07
2        Coffee Shop  0.07
3          Bookstore  0.07
4  Food & Drink Shop  0.07


----BEAUCLERC ROAD----
               venue  freq
0    Harbo

In [52]:
# Define a function to return the most common venues/facilities nearby real estate investments#

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [53]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Street']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

In [54]:
# create a new dataframe
venues_sorted = pd.DataFrame(columns=columns)
venues_sorted['Street'] = london_grouped['Street']

for ind in np.arange(london_grouped.shape[0]):
    venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_grouped.iloc[ind, :], num_top_venues)

In [55]:
venues_sorted.head()


Street 1st Most Common Venue 2nd Most Common Venue  \
0    ALBION SQUARE                  Café     Indian Restaurant   
1      ANHALT ROAD                   Pub     French Restaurant   
2  ANSDELL TERRACE        Clothing Store            Restaurant   
3  APPLEGARTH ROAD        Sandwich Place                Casino   
4  BARONSMEAD ROAD           Pizza Place           Coffee Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Bar            Restaurant           Coffee Shop   
1         Grocery Store                 Plaza           Art Gallery   
2                   Pub             Juice Bar                 Hotel   
3             Nightclub                   Bar  Fast Food Restaurant   
4        Breakfast Spot       Nature Preserve             Bookstore   

  6th Most Common Venue 7th Most Common Venue    8th Most Common Venue  \
0                   Pub                Museum  New American Restaurant   
1                Garden    English Restaurant             Cocktail Bar   
2    Italian Restaurant     Indian Restaurant                   Bakery   
3  Ethiopian Restaurant           Event Space                  Exhibit   
4                  Café        Farmers Market          Thai Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0          Burger Joint                   Park  
1                 Diner   Gym / Fitness Center  
2                   Gym          Grocery Store  
3               Factory     Falafel Restaurant  
4     Food & Drink Shop                   Park

In [56]:
venues_sorted.shape


(150, 11)

In [57]:
london_grouped.shape


(150, 342)

In [58]:
london_grouped=df


In [59]:

#Distribute in 5 Clusters

# set number of clusters
kclusters = 5

london_grouped_clustering = london_grouped.drop('Street', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(london_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:50]

array([1, 3, 0, 3, 2, 1, 2, 0, 0, 1, 3, 3, 3, 1, 2, 2, 1, 3, 0, 1, 4, 4,
       3, 1, 1, 0, 3, 4, 1, 0, 3, 2, 3, 2, 2, 4, 3, 3, 2, 0, 1, 2, 4, 0,
       4, 0, 0, 4, 0, 0], dtype=int32)

In [60]:
#Dataframe to include Clusters

london_grouped_clustering=df
london_grouped_clustering.head()

Street  Avg_Price   Latitude   Longitude
196    ALBION SQUARE  2450000.0 -41.273758  173.289393
390      ANHALT ROAD  2435000.0  51.480316   -0.166801
405  ANSDELL TERRACE  2250000.0  51.499890   -0.189103
422  APPLEGARTH ROAD  2400000.0  53.748654   -0.326670
855  BARONSMEAD ROAD  2375000.0  51.477315   -0.239457

In [61]:
london_grouped_clustering.shape


(162, 4)

In [62]:
df.shape


(162, 4)

In [63]:
london_grouped_clustering.dtypes


Street        object
Avg_Price    float64
Latitude     float64
Longitude    float64
dtype: object

In [64]:
df.dtypes


Street        object
Avg_Price    float64
Latitude     float64
Longitude    float64
dtype: object

In [65]:
# add clustering labels
london_grouped_clustering['Cluster Labels'] = kmeans.labels_

# merge london_grouped with london_data to add latitude/longitude for each neighborhood
london_grouped_clustering = london_grouped_clustering.join(venues_sorted.set_index('Street'), on='Street')

london_grouped_clustering.head(30) # check the last columns!

Street     Avg_Price   Latitude   Longitude  \
196         ALBION SQUARE  2.450000e+06 -41.273758  173.289393   
390           ANHALT ROAD  2.435000e+06  51.480316   -0.166801   
405       ANSDELL TERRACE  2.250000e+06  51.499890   -0.189103   
422       APPLEGARTH ROAD  2.400000e+06  53.748654   -0.326670   
855       BARONSMEAD ROAD  2.375000e+06  51.477315   -0.239457   
981        BEAUCLERC ROAD  2.480000e+06  30.211452  -81.617981   
1102      BELVEDERE DRIVE  2.340000e+06  38.072818  -78.458796   
1215    BICKENHALL STREET  2.208500e+06  51.521201   -0.158908   
1253    BIRCHLANDS AVENUE  2.217000e+06  51.448394   -0.160468   
1553       BRAMPTON GROVE  2.456875e+06  51.589961   -0.318525   
1632    BRIARDALE GARDENS  2.397132e+06  51.560175   -0.195431   
1797             BROOKWAY  2.400000e+06  45.432185 -122.802812   
1914         BURBAGE ROAD  2.445000e+06  52.538507   -1.353674   
1980            BURY WALK  2.492500e+06  52.145529   -0.423593   
2068      CALLCOTT STREET  2.375000e+06  51.508350   -0.198328   
2129    CAMPDEN HILL ROAD  2.379653e+06  51.508111   -0.199667   
2136         CAMPION ROAD  2.461000e+06  43.623321  -70.236225   
2158        CANNING PLACE  2.425000e+06  51.499494   -0.185481   
2225        CARLISLE ROAD  2.200000e+06  43.399438  -79.973215   
2230      CARLTON GARDENS  2.483500e+06 -37.801943  144.971970   
2242        CARLYLE COURT  2.300000e+06  32.972701  -97.173392   
2406       CHALCOT SQUARE  2.286679e+06  51.541088   -0.155928   
2484         CHARLES LANE  2.414000e+06  40.257626  -75.093891   
2562     CHELSEA CRESCENT  2.495000e+06  34.522443  -85.443891   
2606  CHESTER CLOSE NORTH  2.450000e+06  51.529205   -0.145081   
2638         CHEYNE COURT  2.250000e+06  52.035905    0.727612   
2641           CHEYNE ROW  2.410000e+06  51.483717   -0.169603   
2686        CHISWICK MALL  2.287500e+06  51.487994   -0.246605   
2761            CITY ROAD  2.468340e+06  51.529697   -0.097763   
2808     CLARENDON STREET  2.250000e+06  42.284961  -71.345534   

      Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
196                1                  Café     Indian Restaurant   
390                3                   Pub     French Restaurant   
405                0        Clothing Store            Restaurant   
422                3        Sandwich Place                Casino   
855                2           Pizza Place           Coffee Shop   
981                1                   Spa           Pizza Place   
1102               2            Playground                  Pool   
1215               0                  Café             Gastropub   
1253               0                   Pub           Coffee Shop   
1553               1          Food Service          Home Service   
1632               3   Sporting Goods Shop           Coffee Shop   
1797               3                   NaN                   NaN   
1914               3                   Bar    Athletics & Sports   
1980               1           Supermarket    English Restaurant   
2068               2                   Pub                  Park   
2129               2                   Pub         Grocery Store   
2136               1                   Pub                  Food   
2158               3                 Hotel    Italian Restaurant   
2225               0                   NaN                   NaN   
2230               1    Italian Restaurant                  Café   
2242               4                  Farm           Zoo Exhibit   
2406               4                  Café           Coffee Shop   
2484               3   American Restaurant    Photography Studio   
2562               1                   NaN                   NaN   
2606               1                Garden          Cocktail Bar   
2638               0           Coffee Shop      Department Store   
2641               3                  Café                   Pub   
2686               4                   Pub               Brewery   


In [66]:
# Create Map

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(london_grouped_clustering['Latitude'], london_grouped_clustering['Longitude'], london_grouped_clustering['Street'], london_grouped_clustering['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [67]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 0, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
405   2250000.0        Clothing Store            Restaurant   
1215  2208500.0                  Café             Gastropub   
1253  2217000.0                   Pub           Coffee Shop   
2225  2200000.0                   NaN                   NaN   
2638  2250000.0           Coffee Shop      Department Store   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
405                    Pub             Juice Bar                 Hotel   
1215    Italian Restaurant           Pizza Place            Restaurant   
1253                Bakery                  Lake         Train Station   
2225                   NaN                   NaN                   NaN   
2638             Bookstore              Pharmacy                Bakery   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
405     Italian Restaurant     Indian Restaurant                Bakery   
1215                 Hotel                Bakery                   Bar   
1253    Chinese Restaurant               Brewery     French Restaurant   
2225                   NaN                   NaN                   NaN   
2638                  Café  Gym / Fitness Center           Supermarket   

     9th Most Common Venue 10th Most Common Venue  
405                    Gym          Grocery Store  
1215         Movie Theater       Greek Restaurant  
1253     Food & Drink Shop                   Food  
2225                   NaN                    NaN  
2638    Italian Restaurant          Grocery Store

In [68]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 1, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
196   2450000.0                  Café     Indian Restaurant   
981   2480000.0                   Spa           Pizza Place   
1553  2456875.0          Food Service          Home Service   
1980  2492500.0           Supermarket    English Restaurant   
2136  2461000.0                   Pub                  Food   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
196                    Bar            Restaurant           Coffee Shop   
981        Harbor / Marina       Automotive Shop           Zoo Exhibit   
1553           Zoo Exhibit   Filipino Restaurant  Ethiopian Restaurant   
1980           Dry Cleaner           Coffee Shop                  Park   
2136                 Trail           Zoo Exhibit  Fast Food Restaurant   

     6th Most Common Venue 7th Most Common Venue    8th Most Common Venue  \
196                    Pub                Museum  New American Restaurant   
981   Fast Food Restaurant           Event Space                  Exhibit   
1553           Event Space               Exhibit                  Factory   
1980   Rental Car Location  Fast Food Restaurant                     Café   
2136  Ethiopian Restaurant           Event Space                  Exhibit   

     9th Most Common Venue 10th Most Common Venue  
196           Burger Joint                   Park  
981                Factory     Falafel Restaurant  
1553    Falafel Restaurant                   Farm  
1980        Hardware Store                    Pub  
2136               Factory     Falafel Restaurant

In [69]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 2, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
855   2375000.0           Pizza Place           Coffee Shop   
1102  2340000.0            Playground                  Pool   
2068  2375000.0                   Pub                  Park   
2129  2379652.7                   Pub         Grocery Store   
2944  2367500.0                 Hotel                   Pub   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
855         Breakfast Spot       Nature Preserve             Bookstore   
1102   Filipino Restaurant  Ethiopian Restaurant           Event Space   
2068           Yoga Studio                 Hotel         Grocery Store   
2129                 Hotel     Indian Restaurant                Bakery   
2944                Garden                  Café           Coffee Shop   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
855                   Café        Farmers Market       Thai Restaurant   
1102               Exhibit               Factory    Falafel Restaurant   
2068     Indian Restaurant             Bookstore           Coffee Shop   
2129                  Park           Coffee Shop           Yoga Studio   
2944    Italian Restaurant    Chinese Restaurant                   Bar   

         9th Most Common Venue 10th Most Common Venue  
855          Food & Drink Shop                   Park  
1102                      Farm         Farmers Market  
2068          Sushi Restaurant            Record Shop  
2129            Ice Cream Shop        Thai Restaurant  
2944  Mediterranean Restaurant       Tapas Restaurant

In [70]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 3, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
390   2435000.0                   Pub     French Restaurant   
422   2400000.0        Sandwich Place                Casino   
1632  2397132.0   Sporting Goods Shop           Coffee Shop   
1797  2400000.0                   NaN                   NaN   
1914  2445000.0                   Bar    Athletics & Sports   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
390          Grocery Store                 Plaza           Art Gallery   
422              Nightclub                   Bar  Fast Food Restaurant   
1632         Grocery Store  Gym / Fitness Center        Breakfast Spot   
1797                   NaN                   NaN                   NaN   
1914                   Gym         Grocery Store          Dance Studio   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
390                 Garden    English Restaurant          Cocktail Bar   
422   Ethiopian Restaurant           Event Space               Exhibit   
1632  Ethiopian Restaurant               Exhibit               Factory   
1797                   NaN                   NaN                   NaN   
1914           Event Space               Exhibit               Factory   

     9th Most Common Venue 10th Most Common Venue  
390                  Diner   Gym / Fitness Center  
422                Factory     Falafel Restaurant  
1632    Falafel Restaurant                   Farm  
1797                   NaN                    NaN  
1914    Falafel Restaurant                   Farm

In [71]:
london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 4, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
2242  2.300000e+06                  Farm           Zoo Exhibit   
2406  2.286679e+06                  Café           Coffee Shop   
2686  2.287500e+06                   Pub               Brewery   
3377  2.298000e+06                 Hotel           Zoo Exhibit   
4285  2.265000e+06                   Gym                   Pub   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2242   Filipino Restaurant  Ethiopian Restaurant           Event Space   
2406    Italian Restaurant                   Pub                   Bar   
2686             Gift Shop            Art Museum  Gym / Fitness Center   
3377   Filipino Restaurant  Ethiopian Restaurant           Event Space   
4285   American Restaurant                 Trail               Dog Run   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2242               Exhibit               Factory    Falafel Restaurant   
2406     Convenience Store     French Restaurant                  Park   
2686     Food & Drink Shop        Farmers Market  Ethiopian Restaurant   
3377               Exhibit               Factory    Falafel Restaurant   
4285        Farmers Market    English Restaurant  Ethiopian Restaurant   

     9th Most Common Venue 10th Most Common Venue  
2242        Farmers Market   Fast Food Restaurant  
2406            Restaurant       Greek Restaurant  
2686           Event Space                Exhibit  
3377                  Farm         Farmers Market  
4285           Event Space                Exhibit